In [98]:
import os
import random
import pickle
import zipfile
import numpy as np

### HistWords dataset:

In [99]:
# # load dataset from here: https://github.com/williamleif/histwords
# !git clone https://github.com/williamleif/histwords.git
# !wget -O all_english_embeddings.zip "http://snap.stanford.edu/historical_embeddings/eng-all_sgns.zip"

# # unzip loaded dataset
# with zipfile.ZipFile("all_english_embeddings.zip", 'r') as zip_ref:
#     zip_ref.extractall("all_english_embeddings")

## Step 1: Load Word Embeddings

In [100]:
# for loading historical embeddings from .npy files
def load_embeddings(file_path):
    return np.load(file_path)

In [101]:
# base dir for embeddings
base_dir = "all_english_embeddings/sgns"
print(os.getcwd())

/Users/bryan/Documents/College/Computer Science/CMSC 491 - Modern Regression/Project/code


### Obtain subsample of words from dataset:

In [131]:
# specify decades of interest
decades = ['1880', '1890', '1900', '1910', '1920', '1930', '1940', '1950', '1960', '1970', '1980']
vocab_dict = {}
embeddings_dict = {}
random.seed(69)         # set desired seed here
sample_size = 500       # set desired sample size here

In [132]:
# load and optionally sample each decade's embeddings and vocabulary
for decade in decades:
    # load embeddings
    embedding_path = os.path.join(base_dir, f"{decade}-w.npy")
    embeddings = load_embeddings(embedding_path)
    
    # load vocabulary
    vocab_path = os.path.join(base_dir, f"{decade}-vocab.pkl")
    with open(vocab_path, 'rb') as f:
        vocab = pickle.load(f)
    
    # ensure embeddings and vocab are same size
    assert len(embeddings) == len(vocab), f"Mismatch in size for {decade}"
    
    # fill dicts
    embeddings_dict[decade] = embeddings
    vocab_dict[decade] = vocab

### Filter subsamples by intersection across decades:

In [134]:
# obtain common vocabulary across all decades
common_vocab = set(vocab_dict[decades[0]])
for decade in decades[1:]:
    common_vocab.intersection_update(vocab_dict[decade])

common_vocab = list(common_vocab)  # converted to list for indexing

In [135]:
# precompute word_to_index dictionaries for each decade
word_to_index_dict = {}
for decade in decades:
    vocab = vocab_dict[decade]
    word_to_index = {word: idx for idx, word in enumerate(vocab)}
    word_to_index_dict[decade] = word_to_index

# rand sample from common_vocab
initial_sample_size = sample_size * 2  # increase here to account for possible zero vectors
sampled_words = random.sample(common_vocab, min(initial_sample_size, len(common_vocab)))

valid_words = []
zero_vector = np.zeros(embeddings_dict[decades[0]].shape[1])

for word in sampled_words:
    has_zero_vector = False
    for decade in decades:
        idx = word_to_index_dict[decade][word]
        embedding = embeddings_dict[decade][idx]
        if np.array_equal(embedding, zero_vector):
            has_zero_vector = True
            break
    if not has_zero_vector:
        valid_words.append(word)
    if len(valid_words) >= sample_size:
        break  # stop if we have enough valid words

print(f"Number of valid words (non-zero embeddings in all decades): {len(valid_words)}")

# update vocab_dict and embeddings_dict
for decade in decades:
    embeddings = embeddings_dict[decade]
    word_to_index = word_to_index_dict[decade]
    
    # obtain embeddings for valid_words
    indices = [word_to_index[word] for word in valid_words]
    filtered_embeddings = embeddings[indices]
    
    # update dicts with filtered values
    vocab_dict[decade] = valid_words
    embeddings_dict[decade] = filtered_embeddings


Number of valid words (non-zero embeddings in all decades): 261


In [108]:
# debugging
for decade, embeddings in embeddings_dict.items():
    print(f"{decade}'s embeddings:")
    print(f"shape: {embeddings.shape}") # display shape of embeddings per decade
    print(embeddings_dict[decade][:5])  # display first n rows of embeddings per decade
    print()

1880's embeddings:
shape: (261, 300)
[[ 5.89306278e-02  2.63427942e-02  1.71610623e-01 ...  1.58075229e-01
   1.60036059e-04 -1.94007562e-02]
 [ 4.17273530e-02  6.05256095e-02  1.03495172e-01 ...  1.11328742e-01
  -3.27469768e-02 -7.49660381e-03]
 [ 1.16370983e-01  6.21089009e-02  2.79011108e-02 ... -6.96851693e-03
  -1.14058511e-01 -1.93445299e-02]
 [ 6.08386892e-02  4.18023460e-02  3.44829858e-02 ... -4.65702396e-02
   5.28217196e-02 -7.52707786e-02]
 [ 1.76609625e-01  9.88304775e-02 -8.19124244e-02 ...  2.28180647e-02
  -6.16835688e-03 -1.26353976e-01]]

1890's embeddings:
shape: (261, 300)
[[ 0.06258768  0.10097345  0.07172201 ...  0.10582891 -0.04809491
  -0.06341044]
 [ 0.02260715  0.04082878  0.08991884 ...  0.07959534 -0.0429757
   0.03836032]
 [ 0.13185701  0.05263615  0.0215538  ...  0.02891969 -0.0440946
   0.01414854]
 [ 0.05864148  0.0765184   0.01638594 ... -0.04513712  0.09602071
  -0.08103314]
 [ 0.15885009  0.08334426  0.00086667 ... -0.03446826 -0.00241783
   0.012040

## Step 2: Standardize Data

In [109]:
def standardize(data):
    """
    Manually standardizes data by centering (subtracting mean) and scaling (dividing by standard deviation).
    
    Parameters:
    data (numpy.ndarray): Input data matrix of shape (num_vectors, num_dimensions).
    
    Returns:
    standardized_data (numpy.ndarray): Standardized data with zero mean and unit variance.
    mean_vector (numpy.ndarray): Computed mean vector.
    std_vector (numpy.ndarray): Computed standard deviation vector.
    """
    num_vectors, num_dimensions = len(data), len(data[0])
    mean_vector = [0] * num_dimensions
    std_vector = [0] * num_dimensions
    
    # compute mean
    for vector in data:
        mean_vector += vector
    mean_vector /= num_vectors
    
    # compute standard deviation
    for vector in data:
        std_vector += (vector - mean_vector) ** 2
    std_vector = (std_vector / num_vectors) ** 0.5
    
    # avoid division by zero (s.t. if a dimension has zero variance, set std to 1)
    std_vector[std_vector == 0] = 1.0
    
    # center and scale data
    standardized_data = [0] * len(data)
    for i in range(num_vectors):
        standardized_data[i] = (data[i] - mean_vector) / std_vector
    
    return np.array(standardized_data), np.array(mean_vector), np.array(std_vector)

In [110]:
std_embeddings_dict = {}
for decade, embeddings in embeddings_dict.items():
    standardized_data, _, _ = standardize(embeddings_dict[decade])
    std_embeddings_dict[decade] = standardized_data

### Before centering (values small, but not entirely close to zero):

In [111]:
# debugging
for decade, embeddings in embeddings_dict.items():
    _, mean_vector, _ = standardize(embeddings)
    print(f"Mean vector for non-centered embeddings ({decade}'s):")
    print(mean_vector[:5])
    print()

Mean vector for non-centered embeddings (1880's):
[ 0.02415002  0.03659805  0.01104663 -0.00573679 -0.01024766]

Mean vector for non-centered embeddings (1890's):
[ 0.02783459  0.03321555  0.00699224 -0.00405757 -0.01037738]

Mean vector for non-centered embeddings (1900's):
[ 0.02407715  0.03199629  0.00800725 -0.00618739 -0.0037047 ]

Mean vector for non-centered embeddings (1910's):
[ 0.0258846   0.03681539  0.01150072 -0.00855438 -0.00465532]

Mean vector for non-centered embeddings (1920's):
[ 0.0325301   0.04147889  0.00618216 -0.00636544 -0.00575372]

Mean vector for non-centered embeddings (1930's):
[ 0.0284313   0.04351918  0.01426056 -0.00780257 -0.00726101]

Mean vector for non-centered embeddings (1940's):
[ 0.02831436  0.04065627  0.01338011 -0.00597913 -0.00666074]

Mean vector for non-centered embeddings (1950's):
[ 0.0303854   0.04400954  0.01271835 -0.0069191  -0.01150054]

Mean vector for non-centered embeddings (1960's):
[ 0.03169728  0.04228024  0.01320285 -0.007797

### After centering (values now much closer to zero):

In [112]:
# debugging
for decade, embeddings in std_embeddings_dict.items():
    _, mean_vector, _ = standardize(embeddings)
    print(f"Mean vector for centered embeddings ({decade}'s):")
    print(mean_vector[:5])
    print()

Mean vector for centered embeddings (1880's):
[ 1.82059561e-16  3.67947478e-16  2.79682620e-17 -3.57313157e-17
 -5.69999561e-17]

Mean vector for centered embeddings (1890's):
[ 1.70149123e-18 -5.48943607e-16 -8.33730700e-17  2.21193859e-17
 -1.40373026e-17]

Mean vector for centered embeddings (1900's):
[-9.35820174e-18 -3.05417675e-16 -2.84999780e-17 -1.93544627e-17
  5.95521929e-18]

Mean vector for centered embeddings (1910's):
[ 1.15701403e-16  2.49906524e-16  6.80596490e-18 -1.59514802e-17
 -8.50745613e-18]

Mean vector for centered embeddings (1920's):
[-4.88327982e-16  4.38984736e-16  7.65671051e-18  6.38059210e-19
  3.19029605e-17]

Mean vector for centered embeddings (1930's):
[-5.22570493e-16  7.78432236e-17 -5.27462280e-17  1.87164035e-17
 -1.36119298e-17]

Mean vector for centered embeddings (1940's):
[ 2.52671447e-16 -7.73327762e-16 -2.11303942e-16  6.21044297e-17
 -1.59514802e-16]

Mean vector for centered embeddings (1950's):
[-4.70036951e-17 -9.69849999e-17 -1.00441154

## Step 3: Compute Covariance Matrix

In [113]:
def compute_cv_matrix(data):
    """
    Manually computes covariance matrix of input data.
    
    Parameters:
    data (numpy.ndarray): Centered data matrix of shape (num_vectors, num_dimensions).
    
    Returns:
    covariance_matrix (numpy.ndarray): Covariance matrix of shape (num_dimensions, num_dimensions).
    """
    data = np.array(data)
    num_vectors = data.shape[0] # init cv matrix
    covariance_matrix = (data.T @ data) / (num_vectors - 1) # cv cmoputed with matrix multiplication and element-wise averaging

    return covariance_matrix

In [114]:
cv_matrices_dict = {}
for decade, embedding in std_embeddings_dict.items():
    cv_matrices_dict[decade] = compute_cv_matrix(embedding)

In [115]:
# debugging
for decade, matrix in cv_matrices_dict.items():
    print(f"{decade}'s covariance matrix shape: {cv_matrices_dict[decade].shape}")
    # the cv matrix should be symmetric
    print("Is symmetric? ", np.allclose(cv_matrices_dict[decade], cv_matrices_dict[decade].T)) # should print True if symmetric
    print()

1880's covariance matrix shape: (300, 300)
Is symmetric?  True

1890's covariance matrix shape: (300, 300)
Is symmetric?  True

1900's covariance matrix shape: (300, 300)
Is symmetric?  True

1910's covariance matrix shape: (300, 300)
Is symmetric?  True

1920's covariance matrix shape: (300, 300)
Is symmetric?  True

1930's covariance matrix shape: (300, 300)
Is symmetric?  True

1940's covariance matrix shape: (300, 300)
Is symmetric?  True

1950's covariance matrix shape: (300, 300)
Is symmetric?  True

1960's covariance matrix shape: (300, 300)
Is symmetric?  True

1970's covariance matrix shape: (300, 300)
Is symmetric?  True

1980's covariance matrix shape: (300, 300)
Is symmetric?  True



## Step 4: Compute Eigenvalues/Eigenvectors of Covariance Matrix

In [116]:
def random_vector(size):
    """
    Generates a random vector of specified size using Python's random module.
    
    Parameters:
    size (int): Size of random vector.
    
    Returns:
    list: Random vector with values between 0 and 1.
    """
    return [random.random() for _ in range(size)]

In [117]:
def l2_norm(vector):
    """
    Manually computes Euclidean (L2) norm of vector.
    
    Parameters:
    vector (numpy.ndarray): Input vector.
    
    Returns:
    float: Euclidean norm of vector.
    """
    sum_of_squares = 0.0
    for value in vector:
        sum_of_squares += value ** 2
    return sum_of_squares ** 0.5

In [118]:
def power_iteration(matrix, num_iterations=1000, tolerance=1e-9):
    """
    Manually computes largest eigenvalue and its corresponding eigenvector using power iteration.
    
    Parameters:
    matrix (numpy.ndarray): Input square matrix.
    num_iterations (int): Number of iterations to perform.
    tolerance (float): Convergence tolerance.
    
    Returns:
    largest_eigenvalue (float): Largest eigenvalue.
    eigenvector (numpy.ndarray): Corresponding eigenvector.
    """
    # init random vector
    b_k = random_vector(matrix.shape[1])
    
    for _ in range(num_iterations):
        # matrix-vector multiplication
        b_k1 = (matrix @ b_k)

        # normalize vector
        b_k1_norm = l2_norm(b_k1)
        b_k1 = b_k1 / b_k1_norm
        
        # check convergence
        if l2_norm(b_k1 - b_k) < tolerance:
            break
        b_k = b_k1
    
    # compute corresponding eigenvalue
    largest_eigenvalue = (b_k.T @ (matrix @ b_k)) / (b_k.T @ b_k)
    
    return largest_eigenvalue, b_k

In [119]:
# debugging
for decade, matrix in cv_matrices_dict.items():
    largest_eigenvalue, eigenvector = power_iteration(matrix)
    print(f"{decade}'s Largest Eigenvalue:", largest_eigenvalue)
    print()

1880's Largest Eigenvalue: 9.905349657393451

1890's Largest Eigenvalue: 9.908837698643081

1900's Largest Eigenvalue: 9.835365563501123

1910's Largest Eigenvalue: 9.831183793216537

1920's Largest Eigenvalue: 10.224507946791954

1930's Largest Eigenvalue: 10.449914671400288

1940's Largest Eigenvalue: 10.285727534689782

1950's Largest Eigenvalue: 10.05393844778684

1960's Largest Eigenvalue: 10.138958210444516

1970's Largest Eigenvalue: 10.631731023201146

1980's Largest Eigenvalue: 11.088972914133837



## Step 5: Select Largest k Eigenvalues

In [120]:
def largest_k_eigenvalues(matrix, k, num_iterations=1000, tolerance=1e-9):
    """
    Computes largest k eigenvalues and their corresponding eigenvectors using power iteration and deflation.
    
    Parameters:
    matrix (numpy.ndarray): Input square matrix.
    k (int): Number of top eigenvalues/eigenvectors to find.
    num_iterations (int): Number of iterations for each power iteration step.
    tolerance (float): Convergence tolerance for power iteration.
    
    Returns:
    eigenvalues (list): List of top k eigenvalues.
    eigenvectors (list): List of corresponding eigenvectors.
    """
    matrix_copy = matrix[:] # copy of matrix to avoid modifying original
    eigenvalues = []
    eigenvectors = []

    for _ in range(k):
        # find largest eigenvalue and corresponding eigenvector
        largest_eigenvalue, eigenvector = power_iteration(matrix_copy, num_iterations, tolerance)
        eigenvalues.append(largest_eigenvalue)
        eigenvectors.append(eigenvector)

        # deflation step, remove component corresponding to found eigenvector
        matrix_copy = matrix_copy - largest_eigenvalue * np.outer(eigenvector, eigenvector)

    return eigenvalues, np.array(eigenvectors)

In [121]:
# debugging
k = 3
eigenvalues_dict = {}
eigenvectors_dict = {}
for decade, matrix in cv_matrices_dict.items():
    eigenvalues, eigenvectors = largest_k_eigenvalues(matrix, k)
    eigenvalues_dict[decade], eigenvectors_dict[decade] = eigenvalues, eigenvectors
    print(f"{decade}'s largest k = {k} eigenvalues:", eigenvalues)
    print()

1880's largest k = 3 eigenvalues: [9.90534965739344, 9.070473232146858, 7.795668918263916]

1890's largest k = 3 eigenvalues: [9.908837698643083, 9.16906096945435, 7.706751326526973]

1900's largest k = 3 eigenvalues: [9.835365563501128, 8.859096263700168, 8.167323349807027]

1910's largest k = 3 eigenvalues: [9.83118379321654, 9.320788482748409, 7.962031358754424]

1920's largest k = 3 eigenvalues: [10.224507946791952, 9.394343580849894, 7.530727121157983]

1930's largest k = 3 eigenvalues: [10.449914671400293, 9.3521984613467, 7.80599562512588]

1940's largest k = 3 eigenvalues: [10.285727534689777, 9.444062464346135, 7.794353233675874]

1950's largest k = 3 eigenvalues: [10.05393844778684, 9.6486765294748, 7.381857600848164]

1960's largest k = 3 eigenvalues: [10.138958210444514, 9.842937820110349, 7.336385484267628]

1970's largest k = 3 eigenvalues: [10.631731023201144, 9.697477455964638, 7.318787173864057]

1980's largest k = 3 eigenvalues: [11.088972914133835, 9.281243699634365,

## Step 6: Transform Data Onto New Space

In [122]:
def transpose(matrix):
    """
    Manually transposes a given matrix.
    
    Parameters:
    matrix (list of lists): Input matrix for transposition.
    
    Returns:
    transposed (list of lists): Transposed matrix.
    """
    return [[row[i] for row in matrix] for i in range(len(matrix[0]))]

### Before transpose (mismatched dims between data and eigenvectors):

In [123]:
print(f"Shape of standardized data for {decade}: {std_embeddings_dict[decade].shape}")
print(f"Shape of eigenvectors for {decade}: {np.array(eigenvectors_dict[decade]).shape}")

Shape of standardized data for 1980: (261, 300)
Shape of eigenvectors for 1980: (3, 300)


### After transpose (now matching dims between data and eigenvectors):

In [124]:
print(f"Shape of standardized data for {decade}: {std_embeddings_dict[decade].shape}")
print(f"Shape of eigenvectors for {decade}: {np.array(transpose(eigenvectors_dict[decade])).shape}")

Shape of standardized data for 1980: (261, 300)
Shape of eigenvectors for 1980: (300, 3)


In [125]:
transf_embeddings_dict = {}
for decade in decades:
    transformed_data = (std_embeddings_dict[decade] @ transpose(eigenvectors_dict[decade]))
    transf_embeddings_dict[decade] = transformed_data

## Step 7: Plot Resulting Data in Reduced Domain

In [126]:
import plotly.graph_objs as go
import plotly.offline as py

In [127]:
print("Keys in transf_embeddings_dict:", transf_embeddings_dict.keys())


Keys in transf_embeddings_dict: dict_keys(['1880', '1890', '1900', '1910', '1920', '1930', '1940', '1950', '1960', '1970', '1980'])


In [128]:
def interpolate_points(data1, data2, num_interpolations=10):
    """Interpolates between two sets of points."""
    interpolated_data = []
    for alpha in np.linspace(0, 1, num_interpolations):
        interpolated = (1 - alpha) * data1 + alpha * data2
        interpolated_data.append(interpolated)
    return interpolated_data

In [129]:
frames = []
text_size = 8
marker_size = 3
num_interpolations = 20  # adjust for smoother transitions here

for i in range(len(decades) - 1):
    curr_decade = decades[i]
    next_decade = decades[i + 1]
    data1 = embeddings_dict[curr_decade]
    data2 = embeddings_dict[next_decade]
    
    # create interpolated frames
    interpolated_frames = interpolate_points(data1, data2, num_interpolations)
    
    for j, interpolated_data in enumerate(interpolated_frames):
        frame = go.Frame(
            data=[
                go.Scatter3d(
                    x=interpolated_data[:, 0],
                    y=interpolated_data[:, 1],
                    z=interpolated_data[:, 2],
                    mode='markers+text',
                    marker=dict(size=marker_size, color='blue'),
                    text=vocab_dict[curr_decade],
                    textfont=dict(size=text_size),
                    name=f"Interpolation {i}-{j}"
                )
            ],
            name=f"Frame {i}-{j}",
        )
        frames.append(frame)

frames.append(
    go.Frame(
        data=[
            go.Scatter3d(
                x=embeddings_dict[decades[-1]][:, 0],
                y=embeddings_dict[decades[-1]][:, 1],
                z=embeddings_dict[decades[-1]][:, 2],
                mode='markers+text',
                marker=dict(size=marker_size, color='blue'),
                text=vocab_dict[decades[-1]],
                name=decades[-1]
            )
        ],
        name=f"Frame {len(decades) - 1}-0"
    )
)

In [130]:
# fixed axis ranges
x_min, x_max = -0.2, 0.2
y_min, y_max = -0.2, 0.2
z_min, z_max = -0.2, 0.2

axes_intervals = [x_min, -0.1, 0, 0.1, x_max]

layout = go.Layout(
    title="3D Visualization of Word Embeddings Over Time",
    margin=dict(l=0, r=0, b=0, t=40),
    scene=dict(
        xaxis=dict(title="PC1", range=[x_min, x_max], tickvals=axes_intervals, autorange=False),
        yaxis=dict(title="PC2", range=[y_min, y_max], tickvals=axes_intervals, autorange=False),
        zaxis=dict(title="PC3", range=[z_min, z_max], tickvals=axes_intervals, autorange=False),
        aspectmode='manual',
        aspectratio=dict(x=1, y=1, z=1),
    ),
    height=800,
    sliders=[{
        "steps": [
            {
                "args": [[f"Frame {i}-0"], {
                    "frame": {"duration": 100, "redraw": True},
                    "mode": "immediate",
                    "transition": {"duration": 100}
                }],
                "label": f"{decades[i]}",
                "method": "animate"
            }
            for i in range(len(decades))
        ],
        "active": 0,
        "x": 0.2,
        "xanchor": "left",
        "y": 0,
        "yanchor": "top",
        "len": 0.5
    }],
    updatemenus=[{
        "buttons": [
            {
                "args": [None, {
                    "frame": {"duration": 100, "redraw": True},
                    "mode": "immediate",
                    "fromcurrent": True
                }],
                "label": "Play",
                "method": "animate"
            },
            {
                "args": [[None], {
                    "frame": {"duration": 0, "redraw": True},
                    "mode": "immediate",
                    "transition": {"duration": 0}
                }],
                "label": "Pause",
                "method": "animate"
            },
            {
                "args": [[f"Frame 0-0"], {  # reset to first interpolated frame
                    "frame": {"duration": 0, "redraw": True},
                    "mode": "immediate",
                    "transition": {"duration": 0}
                }],
                "label": "Reset",
                "method": "animate"
            }
        ],
        "direction": "left",
        "pad": {"r": 10, "t": 87},
        "showactive": False,
        "type": "buttons",
        "x": 0.1,
        "xanchor": "right",
        "y": 0,
        "yanchor": "top"
    }]
)

fig = go.Figure(data=[frames[0].data[0]], layout=layout, frames=frames)
py.iplot(fig)

## Step 8: Quantitate 